In [1]:
from train import train_model
import load_data_jax_metrics
import training_jax_lossvariance as train
import importlib 
import numpy as np



ModuleNotFoundError: No module named 'Qlstm_Random'

In [2]:
dataset_list=['legendre3','euro','mackey','sp500','btc','sp500_md','btc_md']
sample_size_list=[5,5,4,5,5,5,5] #the sample size for each dataset, for euro and legendre this is 5.  For mackey is 4

qubits_list=[2,4,6,8,10,12] #in the paper we utilize 2,4,6 or 8 
hidden_list=[16]#[16,32,48,64]
key_list=[2,3,4,5,6,7,8,9,0]
kernel_size=2
architecture='super_parallel' #options are no_reupload, parallel and super_parallel
#point_list=[268,518,768,1018,1268,1518,1768,2018,2268,3518,2768,3018,3268,3518,3768,4018]
point_list=[1000]
 # if you want to work with parallel ansatz indicate the number of layers in the loop below in variable n_layers
 

For generating plots of time varying number of points
=======================================================

In [ ]:
times=np.zeros((int(len(point_list)),int(len(key_list))))
for p in range(len(point_list)):  
    points=point_list[p] 
    for k in range(len(key_list)):
        key=key_list[k]
        for d in range(len(dataset_list)):
            dataset=dataset_list[d]
            seq_len=sample_size_list[d]
            
            X_train,Y_train,X_test,Y_test,trainloader,testloader,data,features=load_data_jax_metrics.data(dataset,points)
            print(features)
            target_size=features
            for q in range(len(qubits_list)):
                n_qubits=qubits_list[q]
                if architecture=='super_parallel':
                    n_layers=n_qubits//kernel_size
                elif architecture=='parallel' or architecture=='no_reupload':
                    n_layers=4
                for h in range(len(hidden_list)):
                    concat_size=hidden_list[h]
                    #run_Name=dataset+ansatz+str(out_channels)+str(n_layers)+str(architecture)+str(key)
                    run_name=dataset+str(concat_size)+str(n_qubits)+str(key)+str('Random_Xavier')
                    train.train_model(X_train,Y_train,X_test,Y_test,trainloader,testloader,data,run_name,dataset, seq_len,n_layers,n_qubits,concat_size,target_size,key)
                        

#np.savetxt('times_varyingpoints.csv',times)

1
(1, 5, 1)

Starting epoch 1
Epoch 1: Train Loss = 0.067882, Variance = 1.251774e+01, Validation Loss = 0.050096

Starting epoch 2
Epoch 2: Train Loss = 0.042423, Variance = 5.630685e+00, Validation Loss = 0.033678

Starting epoch 3
Epoch 3: Train Loss = 0.027056, Variance = 2.461169e+00, Validation Loss = 0.022187

Starting epoch 4
Epoch 4: Train Loss = 0.020872, Variance = 1.828517e+00, Validation Loss = 0.019128

Starting epoch 5
Loss Variance (last 5 epochs): 1.54714162e-04
Epoch 5: Train Loss = 0.017925, Variance = 1.296148e+00, Validation Loss = 0.016130

Starting epoch 6
Loss Variance (last 5 epochs): 5.14992426e-05
Epoch 6: Train Loss = 0.014769, Variance = 8.055130e-01, Validation Loss = 0.012729

Starting epoch 7
Loss Variance (last 5 epochs): 2.17334536e-05
Epoch 7: Train Loss = 0.011142, Variance = 3.951663e-01, Validation Loss = 0.008925

Starting epoch 8
Loss Variance (last 5 epochs): 2.12681559e-05
Epoch 8: Train Loss = 0.007784, Variance = 2.127668e-01, Validation Loss

In [ ]:
import matplotlib.pyplot as plt
# Asegurarse de que point_list sea un array de NumPy (si no lo es ya)
point_list = np.array(point_list)

# Configuración de la figura con un DPI de 300
plt.figure(dpi=300)

# Graficar los puntos en el mismo color (ej: azul)
for k in range(len(key_list)):
    plt.plot(point_list, times[:,k], '*', color='blue',markersize=4)

# Etiquetas de los ejes
plt.xlabel('Number of points',fontsize=14)
plt.ylabel('t (s)',fontsize=14)

# Mostrar la gráfica
plt.show()

For generating the plot of the qubits dependence
==================================================

In [11]:
dataset_list=['mackey']
sample_size_list=[4] #the sample size for each dataset, for euro and legendre this is 5.  For mackey is 4
qubits_list=[14,12,10,8,6,4,2] #in the paper we utilize 2,4,6 or 8 
ansatz_list=['basic_layers']
key_list=[1,2,3,4,5,6,7,8,9,0]
kernel_size=2
architecture='super_parallel' #options are no_reupload, parallel and super_parallel
point_list=[268]

In [ ]:
times=np.zeros((int(len(point_list)),int(len(key_list))))
for p in range(len(point_list)):  
    points=point_list[p] 
    for k in range(len(key_list)):
        key=key_list[k]
        for d in range(len(dataset_list)):
            dataset=dataset_list[d]
            l=sample_size_list[d]
            out_size = (l + 2*(1) - kernel_size) // 1 + 1 #since paddding and stride are 1
        
            X_train,Y_train,trainloader,data=load_data_jax.data(dataset,points)
            for q in range(len(qubits_list)):
                out_channels=qubits_list[q]
                if architecture=='super_parallel':
                    n_layers=out_channels//kernel_size
                elif architecture=='parallel' or architecture=='no_reupload':
                    n_layers=4
                for a in range(len(ansatz_list)):
                    ansatz=ansatz_list[a]
                    #run_Name=dataset+ansatz+str(out_channels)+str(n_layers)+str(architecture)+str(key)
                    run_Name='timeC_varyingqubit_1f_withjit_5ep_vect_cpu'
                    time=training_jax.train_testing_phase(X_train,Y_train,kernel_size,n_layers,ansatz,l,out_channels,trainloader,run_Name,dataset,data,architecture,key)
                    times[p,k]=time

np.savetxt('times_varyingqubits.csv',times)

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
times=np.genfromtxt('times_varyingqubits.csv',delimiter=',')
print(times.shape)
# Asegurarse de que point_list sea un array de NumPy (si no lo es ya)
qubits_list = np.array(qubits_list)

# Configuración de la figura con un DPI de 300
plt.figure(dpi=300)

# Graficar los puntos en el mismo color (ej: azul)
for k in range(len(key_list)):
    plt.plot(qubits_list, times[:,k], '*', color='blue',markersize=4)

# Etiquetas de los ejes
plt.xlabel('Number of points',fontsize=14)
plt.ylabel('t (s)',fontsize=14)

# Mostrar la gráfica
plt.show()

Now we calculate for 1 to 5 features

In [ ]:
dataset_list=['sp500','sp500_2d','sp500_3d','sp500_4d','sp500_5d']
sample_size_list=[4,4,4,4,4] #the sample size for each dataset, for euro and legendre this is 5.  For mackey is 4
qubits_list=[6] #in the paper we utilize 2,4,6 or 8 
ansatz_list=['basic_layers']
key_list=[1,2,3,4,5,6,7,8,9,0]
kernel_size=2
architecture='super_parallel' #options are no_reupload, parallel and super_parallel
point_list=[268]

In [ ]:
times=np.zeros((int(len(dataset_list)),int(len(key_list))))
for p in range(len(point_list)):  
    points=point_list[p] 
    for k in range(len(key_list)):
        key=key_list[k]
        for d in range(len(dataset_list)):
            dataset=dataset_list[d]
            l=sample_size_list[d]
            out_size = (l + 2*(1) - kernel_size) // 1 + 1 #since paddding and stride are 1
        
            X_train,Y_train,trainloader,data=load_data_jax.data(dataset,points)
            for q in range(len(qubits_list)):
                out_channels=qubits_list[q]
                if architecture=='super_parallel':
                    n_layers=out_channels//kernel_size
                elif architecture=='parallel' or architecture=='no_reupload':
                    n_layers=4
                for a in range(len(ansatz_list)):
                    ansatz=ansatz_list[a]
                    #run_Name=dataset+ansatz+str(out_channels)+str(n_layers)+str(architecture)+str(key)
                    run_Name='timeC_varyingqubit_1f_withjit_5ep_vect_cpu'
                    time=training_jax.train_testing_phase(X_train,Y_train,kernel_size,n_layers,ansatz,l,out_channels,trainloader,run_Name,dataset,data,architecture,key)
                    times[d,k]=time

np.savetxt('times_varyingqubits.csv',times)

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

# Asegurarse de que features_list sea un array de NumPy (si no lo es ya)
features_list = [1, 2, 3, 4, 5]
features_list = np.array(features_list)

# Configuración de la figura con un DPI de 300
plt.figure(dpi=300)

# Graficar los puntos en el mismo color (ej: azul)
for k in range(times.shape[1]):  # Suponiendo que `times` es una matriz de NumPy
    plt.plot(features_list, times[:, k], '*', color='blue', markersize=4)

# Etiquetas de los ejes
plt.xlabel('Number of features', fontsize=14)
plt.ylabel('t (s)', fontsize=14)

# Configurar solo valores enteros en el eje x
plt.xticks(features_list)

# Mostrar la gráfica
plt.show()
